In [330]:
#load in packages
import pandas as pd
import numpy as np
from scipy import stats as st
import plotly.express as px

In [331]:
#read in csv
df = pd.read_csv('c:/Users/dillo/Documents/Triple10/Sprint-4/4-proj/vehicles_us.csv')
df.head()

price  model_year           model  condition  cylinders fuel  odometer  \
0   9400      2011.0          bmw x5       good        6.0  gas  145000.0   
1  25500         NaN      ford f-150       good        6.0  gas   88705.0   
2   5500      2013.0  hyundai sonata   like new        4.0  gas  110000.0   
3   1500      2003.0      ford f-150       fair        8.0  gas       NaN   
4  14900      2017.0    chrysler 200  excellent        4.0  gas   80903.0   

  transmission    type paint_color  is_4wd date_posted  days_listed  
0    automatic     SUV         NaN     1.0  2018-06-23           19  
1    automatic  pickup       white     1.0  2018-10-19           50  
2    automatic   sedan         red     NaN  2019-02-07           79  
3    automatic  pickup         NaN     NaN  2019-03-22            9  
4    automatic   sedan       black     NaN  2019-04-02           28

# Data Cleaning

### 1. Null Values

In [332]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 51525 entries, 0 to 51524
Data columns (total 13 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   price         51525 non-null  int64  
 1   model_year    47906 non-null  float64
 2   model         51525 non-null  object 
 3   condition     51525 non-null  object 
 4   cylinders     46265 non-null  float64
 5   fuel          51525 non-null  object 
 6   odometer      43633 non-null  float64
 7   transmission  51525 non-null  object 
 8   type          51525 non-null  object 
 9   paint_color   42258 non-null  object 
 10  is_4wd        25572 non-null  float64
 11  date_posted   51525 non-null  object 
 12  days_listed   51525 non-null  int64  
dtypes: float64(4), int64(2), object(7)
memory usage: 5.1+ MB


In [333]:
#check for duplicate records
df.duplicated().sum()

0

In [334]:
#look for null values
df.isna().sum()

price               0
model_year       3619
model               0
condition           0
cylinders        5260
fuel                0
odometer         7892
transmission        0
type                0
paint_color      9267
is_4wd          25953
date_posted         0
days_listed         0
dtype: int64

<div class="alert alert-block alert-info">
Null values identified in 5 columns. 
</div>

In [335]:
#remove records with null values in model_year column as that would hinder analysis and check df null values
df = df.dropna(subset=['model_year'])
df.isna().sum()

price               0
model_year          0
model               0
condition           0
cylinders        4897
fuel                0
odometer         7343
transmission        0
type                0
paint_color      8615
is_4wd          24142
date_posted         0
days_listed         0
dtype: int64


<div class="alert alert-block alert-info">
Will now check to see if null values in cylinders column correspond with electric cars 
</div>

In [336]:
#find out values in fuel column in order to know what to filter for
df['fuel'].unique()

array(['gas', 'diesel', 'other', 'hybrid', 'electric'], dtype=object)

In [337]:
#filter for electric values in fuel column
df[df['fuel'] == 'electric']

price  model_year                model  condition  cylinders      fuel  \
2432    7900      2011.0         toyota prius       good        NaN  electric   
9626       1      2018.0  chevrolet silverado        new       10.0  electric   
20988  10200      2008.0        toyota tundra  excellent        8.0  electric   
22190  15000      2017.0           ford focus   like new        NaN  electric   
46423   4400      2008.0     chevrolet impala  excellent        6.0  electric   
49643   4700      2007.0         toyota prius  excellent        4.0  electric   

       odometer transmission       type paint_color  is_4wd date_posted  \
2432    78466.0    automatic      sedan         NaN     NaN  2018-09-13   
9626    30000.0    automatic      truck         red     1.0  2018-11-21   
20988  131984.0    automatic      truck         NaN     1.0  2019-02-19   
22190   12000.0    automatic  hatchback       white     NaN  2018-11-16   
46423       NaN    automatic      other         red     NaN  2018-11-19   
49643  134000.0    automatic  hatchback      custom     NaN  2019-02-18   

       days_listed  
2432            34  
9626            64  
20988           20  
22190           66  
46423           36  
49643           39

<div class="alert alert-block alert-info">
This data contains electric cars with cylinders. This does not make sense as fully electric cars do not have cylinders, the engine is not a combustion engine.
</div>

In [338]:
#filter for records with electric fuel values and non-null cylinder values
df[(df['fuel'] == 'electric') & (df['cylinders'].isna() == False)]

price  model_year                model  condition  cylinders      fuel  \
9626       1      2018.0  chevrolet silverado        new       10.0  electric   
20988  10200      2008.0        toyota tundra  excellent        8.0  electric   
46423   4400      2008.0     chevrolet impala  excellent        6.0  electric   
49643   4700      2007.0         toyota prius  excellent        4.0  electric   

       odometer transmission       type paint_color  is_4wd date_posted  \
9626    30000.0    automatic      truck         red     1.0  2018-11-21   
20988  131984.0    automatic      truck         NaN     1.0  2019-02-19   
46423       NaN    automatic      other         red     NaN  2018-11-19   
49643  134000.0    automatic  hatchback      custom     NaN  2019-02-18   

       days_listed  
9626            64  
20988           20  
46423           36  
49643           39

In [339]:
#if record has electric fuel value and non-null cylinder value, change fuel value to 'hybrid'
df.loc[df['cylinders'].isna() == False & (df['fuel'] == 'electric'), 'fuel'] = 'hybrid'
df[(df['fuel'] == 'electric') & (df['cylinders'].isna() == False)]


Empty DataFrame
Columns: [price, model_year, model, condition, cylinders, fuel, odometer, transmission, type, paint_color, is_4wd, date_posted, days_listed]
Index: []

In [340]:
#for remaining electric fuel values, change null cylinder values to 0
df.loc[df['fuel'] == 'electric', 'cylinders'] = 0
df.loc[df['fuel'] == 'electric']

price  model_year         model condition  cylinders      fuel  \
2432    7900      2011.0  toyota prius      good        0.0  electric   
22190  15000      2017.0    ford focus  like new        0.0  electric   

       odometer transmission       type paint_color  is_4wd date_posted  \
2432    78466.0    automatic      sedan         NaN     NaN  2018-09-13   
22190   12000.0    automatic  hatchback       white     NaN  2018-11-16   

       days_listed  
2432            34  
22190           66

In [341]:
#drop remaining records will null values in cylinders column and check df null values
df = df.dropna(subset=['cylinders'])
df.isna().sum()

price               0
model_year          0
model               0
condition           0
cylinders           0
fuel                0
odometer         6590
transmission        0
type                0
paint_color      7717
is_4wd          21641
date_posted         0
days_listed         0
dtype: int64

In [342]:
#change cylinders values to int to remove decimal point
df['cylinders'] = df['cylinders'].astype(int)
df['cylinders'].unique()

array([ 6,  4,  8,  5, 10,  3,  0, 12])

In [343]:
#check odometer null values
df[df['odometer'].isna()]

price  model_year                model  condition  cylinders    fuel  \
3       1500      2003.0           ford f-150       fair          8  hybrid   
15     17990      2013.0             ram 1500  excellent          8  hybrid   
23      7500      2004.0        jeep wrangler       good          6  hybrid   
24      3950      2009.0         chrysler 200  excellent          4  hybrid   
25     11499      2017.0     chevrolet malibu   like new          4  hybrid   
...      ...         ...                  ...        ...        ...     ...   
51498  15900      2011.0      gmc sierra 1500  excellent          8  hybrid   
51507  29500      2012.0        toyota tundra       good          8  hybrid   
51516   8999      2011.0  jeep grand cherokee       good          6  hybrid   
51519  11750      2015.0         honda accord  excellent          4  hybrid   
51524   6300      2014.0        nissan altima       good          4  hybrid   

       odometer transmission    type paint_color  is_4wd date_posted  \
3           NaN    automatic  pickup         NaN     NaN  2019-03-22   
15          NaN    automatic  pickup         red     1.0  2018-05-15   
23          NaN    automatic     SUV         red     1.0  2018-05-17   
24          NaN    automatic   sedan         red     NaN  2018-06-11   
25          NaN    automatic   sedan         NaN     NaN  2018-07-26   
...         ...          ...     ...         ...     ...         ...   
51498       NaN    automatic   truck         NaN     1.0  2019-01-25   
51507       NaN    automatic  pickup        grey     1.0  2018-05-01   
51516       NaN    automatic     SUV       white     1.0  2018-11-01   
51519       NaN    automatic   coupe         NaN     NaN  2018-11-24   
51524       NaN    automatic   sedan         NaN     NaN  2018-06-05   

       days_listed  
3                9  
15             111  
23              39  
24              40  
25              43  
...            ...  
51498           69  
51507           31  
51516           51  
51519           89  
51524           10  

[6590 rows x 13 columns]

<div class="alert alert-block alert-info">
The odometer value should not be 0, so records will null odometer values will be removed instead of replaced with 0 value to allow for accurate numerical analysis.
</div>

In [344]:
#drop records with null values in odometer column and check df null values
df = df.dropna(subset=['odometer'])
df.isna().sum()

price               0
model_year          0
model               0
condition           0
cylinders           0
fuel                0
odometer            0
transmission        0
type                0
paint_color      6504
is_4wd          18305
date_posted         0
days_listed         0
dtype: int64

In [345]:
#check unique is_4wd values
df['is_4wd'].unique()

array([ 1., nan])

In [346]:
#replace null is_4wd values with 0
df['is_4wd'] = df['is_4wd'].fillna(0)
df['is_4wd'].unique()

array([1., 0.])

In [347]:
#change is_4wd values to int to remove decimal
df['is_4wd'] = df['is_4wd'].astype(int)
df['is_4wd'].unique()

array([1, 0])

In [348]:
#check df null values
df.isna().sum()

price              0
model_year         0
model              0
condition          0
cylinders          0
fuel               0
odometer           0
transmission       0
type               0
paint_color     6504
is_4wd             0
date_posted        0
days_listed        0
dtype: int64

<div class="alert alert-block alert-info">
Analysis based on paint_color is not as important, so for now null paint_color values will be replaced with 'unknown' to keep a larger sample size for analysis in other categories.
</div>

In [349]:
#replace null paint_color values with 'unknown' and check unique paint_color values
df['paint_color'] = df['paint_color'].fillna('unknown')
df['paint_color'].unique()

array(['unknown', 'red', 'black', 'white', 'grey', 'silver', 'custom',
       'orange', 'yellow', 'blue', 'brown', 'green', 'purple'],
      dtype=object)

In [350]:
#check df null values
df.isna().sum()

price           0
model_year      0
model           0
condition       0
cylinders       0
fuel            0
odometer        0
transmission    0
type            0
paint_color     0
is_4wd          0
date_posted     0
days_listed     0
dtype: int64

### 2. Dates

In [351]:
#check df values
df.head()

price  model_year           model  condition  cylinders    fuel  odometer  \
0   9400      2011.0          bmw x5       good          6  hybrid  145000.0   
2   5500      2013.0  hyundai sonata   like new          4  hybrid  110000.0   
4  14900      2017.0    chrysler 200  excellent          4  hybrid   80903.0   
5  14990      2014.0    chrysler 300  excellent          6  hybrid   57954.0   
6  12990      2015.0    toyota camry  excellent          4  hybrid   79212.0   

  transmission   type paint_color  is_4wd date_posted  days_listed  
0    automatic    SUV     unknown       1  2018-06-23           19  
2    automatic  sedan         red       0  2019-02-07           79  
4    automatic  sedan       black       0  2019-04-02           28  
5    automatic  sedan       black       1  2018-06-20           15  
6    automatic  sedan       white       0  2018-12-27           73

In [352]:
#convert date_posted values to datetime format and check df values
df['date_posted'] = pd.to_datetime(df['date_posted'], format='%Y-%m-%d')
df.head()

price  model_year           model  condition  cylinders    fuel  odometer  \
0   9400      2011.0          bmw x5       good          6  hybrid  145000.0   
2   5500      2013.0  hyundai sonata   like new          4  hybrid  110000.0   
4  14900      2017.0    chrysler 200  excellent          4  hybrid   80903.0   
5  14990      2014.0    chrysler 300  excellent          6  hybrid   57954.0   
6  12990      2015.0    toyota camry  excellent          4  hybrid   79212.0   

  transmission   type paint_color  is_4wd date_posted  days_listed  
0    automatic    SUV     unknown       1  2018-06-23           19  
2    automatic  sedan         red       0  2019-02-07           79  
4    automatic  sedan       black       0  2019-04-02           28  
5    automatic  sedan       black       1  2018-06-20           15  
6    automatic  sedan       white       0  2018-12-27           73

In [353]:
#change model_year values to int to remove decimal point and check df values
df['model_year'] = df['model_year'].astype(int)
df.head()

price  model_year           model  condition  cylinders    fuel  odometer  \
0   9400        2011          bmw x5       good          6  hybrid  145000.0   
2   5500        2013  hyundai sonata   like new          4  hybrid  110000.0   
4  14900        2017    chrysler 200  excellent          4  hybrid   80903.0   
5  14990        2014    chrysler 300  excellent          6  hybrid   57954.0   
6  12990        2015    toyota camry  excellent          4  hybrid   79212.0   

  transmission   type paint_color  is_4wd date_posted  days_listed  
0    automatic    SUV     unknown       1  2018-06-23           19  
2    automatic  sedan         red       0  2019-02-07           79  
4    automatic  sedan       black       0  2019-04-02           28  
5    automatic  sedan       black       1  2018-06-20           15  
6    automatic  sedan       white       0  2018-12-27           73

### 3. Additional

<div class="alert alert-block alert-info">
Model values include brand and model. Brand and model should be split into separate columns for better analysis.
</div>

In [354]:
#split model values into two columns of brand values and car_model values, and check df values
df[['brand', 'car_model']] = df['model'].str.split(' ', n=1, expand=True)
df.head()

price  model_year           model  condition  cylinders    fuel  odometer  \
0   9400        2011          bmw x5       good          6  hybrid  145000.0   
2   5500        2013  hyundai sonata   like new          4  hybrid  110000.0   
4  14900        2017    chrysler 200  excellent          4  hybrid   80903.0   
5  14990        2014    chrysler 300  excellent          6  hybrid   57954.0   
6  12990        2015    toyota camry  excellent          4  hybrid   79212.0   

  transmission   type paint_color  is_4wd date_posted  days_listed     brand  \
0    automatic    SUV     unknown       1  2018-06-23           19       bmw   
2    automatic  sedan         red       0  2019-02-07           79   hyundai   
4    automatic  sedan       black       0  2019-04-02           28  chrysler   
5    automatic  sedan       black       1  2018-06-20           15  chrysler   
6    automatic  sedan       white       0  2018-12-27           73    toyota   

  car_model  
0        x5  
2    sonata  
4       200  
5       300  
6     camry

In [355]:
#check uniformity of brand values
df['brand'].unique()

array(['bmw', 'hyundai', 'chrysler', 'toyota', 'honda', 'kia',
       'chevrolet', 'ram', 'gmc', 'jeep', 'ford', 'nissan', 'subaru',
       'dodge', 'acura', 'cadillac', 'volkswagen', 'buick'], dtype=object)

In [356]:
#drop redundant model column and check df values
df = df.drop('model', axis=1)
df.head()

price  model_year  condition  cylinders    fuel  odometer transmission  \
0   9400        2011       good          6  hybrid  145000.0    automatic   
2   5500        2013   like new          4  hybrid  110000.0    automatic   
4  14900        2017  excellent          4  hybrid   80903.0    automatic   
5  14990        2014  excellent          6  hybrid   57954.0    automatic   
6  12990        2015  excellent          4  hybrid   79212.0    automatic   

    type paint_color  is_4wd date_posted  days_listed     brand car_model  
0    SUV     unknown       1  2018-06-23           19       bmw        x5  
2  sedan         red       0  2019-02-07           79   hyundai    sonata  
4  sedan       black       0  2019-04-02           28  chrysler       200  
5  sedan       black       1  2018-06-20           15  chrysler       300  
6  sedan       white       0  2018-12-27           73    toyota     camry

In [357]:
#check uniformity of condition values
df['condition'].unique()

array(['good', 'like new', 'excellent', 'fair', 'salvage', 'new'],
      dtype=object)

In [358]:
#check uniformity of transmission values
df['transmission'].unique()

array(['automatic', 'manual', 'other'], dtype=object)

In [359]:
#check uniformity of type values
df['type'].unique()

array(['SUV', 'sedan', 'pickup', 'truck', 'coupe', 'hatchback', 'van',
       'wagon', 'mini-van', 'convertible', 'other', 'bus', 'offroad'],
      dtype=object)

<div class="alert alert-block alert-info">
Data looks ready for analysis
</div>

# EDA

In [360]:
#view df
df.head()

price  model_year  condition  cylinders    fuel  odometer transmission  \
0   9400        2011       good          6  hybrid  145000.0    automatic   
2   5500        2013   like new          4  hybrid  110000.0    automatic   
4  14900        2017  excellent          4  hybrid   80903.0    automatic   
5  14990        2014  excellent          6  hybrid   57954.0    automatic   
6  12990        2015  excellent          4  hybrid   79212.0    automatic   

    type paint_color  is_4wd date_posted  days_listed     brand car_model  
0    SUV     unknown       1  2018-06-23           19       bmw        x5  
2  sedan         red       0  2019-02-07           79   hyundai    sonata  
4  sedan       black       0  2019-04-02           28  chrysler       200  
5  sedan       black       1  2018-06-20           15  chrysler       300  
6  sedan       white       0  2018-12-27           73    toyota     camry

In [361]:
#initial descriptive stats
df.describe()

price    model_year     cylinders       odometer        is_4wd  \
count   36421.000000  36421.000000  36421.000000   36421.000000  36421.000000   
mean    12187.634908   2009.753659      6.132259  115319.783834      0.497405   
min         1.000000   1908.000000      0.000000       0.000000      0.000000   
25%      5000.000000   2006.000000      4.000000   69854.000000      0.000000   
50%      9000.000000   2011.000000      6.000000  113000.000000      0.000000   
75%     16900.000000   2014.000000      8.000000  155000.000000      1.000000   
max    375000.000000   2019.000000     12.000000  990000.000000      1.000000   
std     10076.498818      6.265251      1.660223   65069.402417      0.500000   

                         date_posted   days_listed  
count                          36421  36421.000000  
mean   2018-10-25 03:09:11.253398016     39.650367  
min              2018-05-01 00:00:00      0.000000  
25%              2018-07-29 00:00:00     19.000000  
50%              2018-10-25 00:00:00     33.000000  
75%              2019-01-21 00:00:00     53.000000  
max              2019-04-19 00:00:00    271.000000  
std                              NaN     28.118973

<div class="alert alert-block alert-info">
Potential relationships to explore:<br>
- brand/type<br>
- brand/price<br>
- model_year/condition<br>
- model_year/price<br>
- price/transmission<br>
- price/condition<br>
- price/is_4wd<br>
- odometer/model_year<br>
- type/price<br>
- type/odometer<br>
- type/fuel<br>
- type/days_listed<br>
- brand/days_listed<br>
- fuel/days_listed<br>
</div>

In [367]:
#histogram showing distribution of brand of car listings
fig2 = px.histogram(df, x='brand')
fig2.show()

In [371]:
#histogram showing average odometer value per car type
fig3 = px.histogram(df, x='type', y='odometer', histfunc='avg')
fig3.show()

In [373]:
fig4 = px.histogram(df, x='brand', y='days_listed', histfunc='avg')
fig4.show()

In [390]:
sedan = df[df['type']=='sedan']
fig5 = px.histogram(sedan, x='brand', y='odometer', histfunc='avg')
fig5.show()

In [417]:
#create histogram that compares average prices between types of cars made by Toyota and Honda
brands = ['toyota', 'honda',]
types = ['sedan', 'truck', 'SUV', 'hatchback']
df2 = df[df['brand'].isin(brands) & (df['type'].isin(types))]
figg = px.histogram(df2, x='type', y='price', color='brand', histfunc='avg')
figg.show()

In [ ]:
df.head()

price  model_year  condition  cylinders    fuel  odometer transmission  \
0   9400        2011       good          6  hybrid  145000.0    automatic   
2   5500        2013   like new          4  hybrid  110000.0    automatic   
4  14900        2017  excellent          4  hybrid   80903.0    automatic   
5  14990        2014  excellent          6  hybrid   57954.0    automatic   
6  12990        2015  excellent          4  hybrid   79212.0    automatic   

    type paint_color  is_4wd date_posted  days_listed     brand car_model  
0    SUV     unknown       1  2018-06-23           19       bmw        x5  
2  sedan         red       0  2019-02-07           79   hyundai    sonata  
4  sedan       black       0  2019-04-02           28  chrysler       200  
5  sedan       black       1  2018-06-20           15  chrysler       300  
6  sedan       white       0  2018-12-27           73    toyota     camry

In [434]:
fig6 = px.scatter_matrix(df, dimensions = ['model_year', 'price', 'odometer'])
fig6.show()

In [448]:

df1 = df[df['brand']=='ford']
fig7 = px.scatter(df1, x='price', y='days_listed', color='car_model', opacity=.8)
fig7.show()

In [444]:
import sweetviz as sv
my_report = sv.analyze(df)
my_report.show_html() # Default arguments will generate to "SWEETVIZ_REPORT.html"

                                             |          | [  0%]   00:00 -> (? left)

Report SWEETVIZ_REPORT.html was generated! NOTEBOOK/COLAB USERS: the web browser MAY not pop up, regardless, the report IS saved in your notebook/colab files.
